# Inspector

#### What is inspector ?  
   Vai_q_pytorch provides a function called inspector to help users diagnose neural network (NN) models under different device architectures. The inspector can predict target device assignments based on hardware constraints.The generated inspection report can be used to guide  users to modify or optimize the NN model, greatly reducing the difficulty and time of deployment. It is recommended to inspect float models before quantization.

In [1]:
import torch

import sys
import os
os.environ["CUDA_VISIBLE_DEVICES"]="0"

device = torch.device("cuda:0" if torch.cuda.is_available() else "cpu")

if torch.cuda.is_available():
    print("Available GPUs:", torch.cuda.device_count())
    for i in range(torch.cuda.device_count()):
        print(f"GPU {i}: {torch.cuda.get_device_name(i)}")
else:
    print("No GPUs available, CPU {} ".format(device))

yolov5_dir = '/workspace/workspace/YOLO/YOLOv5'
sys.path.append(yolov5_dir)
os.chdir(yolov5_dir)
import utils
display = utils.notebook_init()  # checks

YOLOv5 🚀 v7.0-372-ga3555241 Python-3.8.6 torch-1.13.1+cu117 CUDA:0 (NVIDIA GeForce RTX 3080, 12287MiB)


Setup complete ✅ (8 CPUs, 47.1 GB RAM, 392.4/1006.9 GB disk)


In [2]:
# Import inspector API
# 
# Note:
# You can ignore warning message related with XIR. 
# The inspector relies on 'vai_utf' package. In conda env vitis-ai-pytorch in Vitis-AI docker, vai_utf is ready. But if vai_q_pytorch is installed by source code, it needs to install vai_utf in advance.
from pytorch_nndct import Inspector


[VAIQ_NOTE]: Loading NNDCT kernels...


In [3]:
model_dir = 'jupyter_notebooks/dms_yolov5n/dms_yolov5nLeaky.pt'

In [4]:
# Define a toy neural network
model = torch.hub.load('.', 'custom', path=model_dir, source='local', autoshape=False)  # Load custom model from local path, ensure reloading is controlled
# model = torch.hub.load('.', 'custom', path=model_dir, source='local')  # Load custom model from local path, ensure reloading is controlled

YOLOv5 🚀 v7.0-372-ga3555241 Python-3.8.6 torch-1.13.1+cu117 CUDA:0 (NVIDIA GeForce RTX 3080, 12287MiB)



In [5]:
model = model.to(device)

In [6]:
from torchinfo import summary
summary(model, (1, 3, 480, 480))  # Display model summary for specified input size

Layer (type:depth-idx)                                  Output Shape              Param #
DetectMultiBackend                                      [1, 42, 60, 60]           --
├─DetectionModel: 1-1                                   [1, 42, 60, 60]           --
│    └─Sequential: 2-1                                  --                        --
│    │    └─Conv: 3-1                                   [1, 16, 240, 240]         (1,760)
│    │    └─C3: 3-109                                   --                        (recursive)
│    │    └─Conv: 3-3                                   [1, 32, 120, 120]         (4,672)
│    │    └─C3: 3-109                                   --                        (recursive)
│    │    └─C3: 3-5                                     [1, 32, 120, 120]         (4,800)
│    │    └─C3: 3-109                                   --                        (recursive)
│    │    └─C3: 3-13                                    --                        (recursive)
│    │   

In [7]:
# Specify a target name or fingerprint you want to deploy on
target = "DPUCZDX8G_ISA1_B4096"
# Initialize inspector with target
inspector = Inspector(target)


[VAIQ_NOTE]: Inspector is on.


In [8]:
# Start to inspect the float model
# Note: visualization of inspection results relies on the dot engine.If you don't install dot successfully, set 'image_format = None' when inspecting.
dummy_input = torch.randn(1, 3, 480, 480)
inspector.inspect(model, (dummy_input,), device=device, output_dir="inspect", image_format="png") 


[VAIQ_NOTE]: =>Start to inspect model...

[VAIQ_NOTE]: =>Quant Module is in 'cuda'.

[VAIQ_NOTE]: =>Parsing DetectMultiBackend...

[VAIQ_NOTE]: Start to trace and freeze model...

[VAIQ_NOTE]: The input model nndct_st_DetectMultiBackend_ed is torch.nn.Module.

[VAIQ_NOTE]: Finish tracing.

[VAIQ_NOTE]: Processing ops...


██████████████████████████████████████████████████| 201/201 [00:00<00:00, 1169.91it/s, OpInfo: name = return_0, type = Return]           



[VAIQ_NOTE]: =>Doing weights equalization...

[VAIQ_WARN][QUANTIZER_TORCH_LEAKYRELU]: Preserve negative_slope(0.1015625) of LeakyReLU without quantization.

[VAIQ_NOTE]: =>Quantizable module is generated.(inspect/DetectMultiBackend.py)

[VAIQ_NOTE]: Find subgraph for convlike_fix_18:
node name:DetectMultiBackend::DetectMultiBackend/DetectionModel[model]/C3[model]/C3[2]/Conv[cv2]/Conv2d[conv]/ret.25, op type:nndct_conv2d, output shape: [1, 120, 120, 16]
node name:DetectMultiBackend::DetectMultiBackend/DetectionModel[model]/C3[model]/C3[2]/Conv[cv2]/LeakyReLU[act]/13446, op type:nndct_leaky_relu, output shape: [1, 120, 120, 16]



[VAIQ_NOTE]: Find subgraph for convlike_fix_18:
node name:DetectMultiBackend::DetectMultiBackend/DetectionModel[model]/C3[model]/C3[23]/Sequential[m]/Bottleneck[0]/Conv[cv1]/Conv2d[conv]/ret.257, op type:nndct_conv2d, output shape: [1, 15, 15, 128]
node name:DetectMultiBackend::DetectMultiBackend/DetectionModel[model]/C3[model]/C3[23]/Sequential[m]/Bottleneck[

I20241110 00:52:34.438796   588 compile_pass_manager.cpp:352] [UNILOG][INFO] Compile mode: dpu
I20241110 00:52:34.438834   588 compile_pass_manager.cpp:353] [UNILOG][INFO] Debug mode: null
I20241110 00:52:34.438843   588 compile_pass_manager.cpp:357] [UNILOG][INFO] Target architecture: DPUCZDX8G_ISA1_B4096
I20241110 00:52:34.438891   588 compile_pass_manager.cpp:465] [UNILOG][INFO] Graph name: nndct_conv2d_nndct_leaky_relu_XELApt8ThaWZsdKm, with op num: 9
I20241110 00:52:34.438895   588 compile_pass_manager.cpp:478] [UNILOG][INFO] Begin to compile...
I20241110 00:52:34.441349   588 compile_pass_manager.cpp:489] [UNILOG][INFO] Total device subgraph number 3, DPU subgraph number 1
I20241110 00:52:34.441365   588 compile_pass_manager.cpp:504] [UNILOG][INFO] Compile done.
I20241110 00:52:34.444171   588 compile_pass_manager.cpp:352] [UNILOG][INFO] Compile mode: dpu
I20241110 00:52:34.444198   588 compile_pass_manager.cpp:353] [UNILOG][INFO] Debug mode: null
I20241110 00:52:34.444204   588 


[VAIQ_NOTE]: Find subgraph for convlike_fix_18:
node name:DetectMultiBackend::DetectMultiBackend/DetectionModel[model]/C3[model]/C3[6]/Sequential[m]/Bottleneck[2]/Conv[cv1]/Conv2d[conv]/ret.101, op type:nndct_conv2d, output shape: [1, 30, 30, 64]
node name:DetectMultiBackend::DetectMultiBackend/DetectionModel[model]/C3[model]/C3[6]/Sequential[m]/Bottleneck[2]/Conv[cv1]/LeakyReLU[act]/13930, op type:nndct_leaky_relu, output shape: [1, 30, 30, 64]



[VAIQ_NOTE]: Find subgraph for convlike_fix_18:
node name:DetectMultiBackend::DetectMultiBackend/DetectionModel[model]/C3[model]/C3[6]/Sequential[m]/Bottleneck[1]/Conv[cv2]/Conv2d[conv]/ret.95, op type:nndct_conv2d, output shape: [1, 30, 30, 64]
node name:DetectMultiBackend::DetectMultiBackend/DetectionModel[model]/C3[model]/C3[6]/Sequential[m]/Bottleneck[1]/Conv[cv2]/LeakyReLU[act]/13898, op type:nndct_leaky_relu, output shape: [1, 30, 30, 64]



[VAIQ_NOTE]: Find subgraph for convlike_fix_18:
node name:DetectMultiBackend::DetectMultiBacke

I20241110 00:52:34.643573   588 compile_pass_manager.cpp:352] [UNILOG][INFO] Compile mode: dpu
I20241110 00:52:34.643596   588 compile_pass_manager.cpp:353] [UNILOG][INFO] Debug mode: null
I20241110 00:52:34.643601   588 compile_pass_manager.cpp:357] [UNILOG][INFO] Target architecture: DPUCZDX8G_ISA1_B4096
I20241110 00:52:34.643627   588 compile_pass_manager.cpp:465] [UNILOG][INFO] Graph name: nndct_conv2d_nndct_leaky_relu_LfSDVtWmzEBp7iq8, with op num: 9
I20241110 00:52:34.643630   588 compile_pass_manager.cpp:478] [UNILOG][INFO] Begin to compile...
I20241110 00:52:34.649107   588 compile_pass_manager.cpp:489] [UNILOG][INFO] Total device subgraph number 3, DPU subgraph number 1
I20241110 00:52:34.649123   588 compile_pass_manager.cpp:504] [UNILOG][INFO] Compile done.
I20241110 00:52:34.651897   588 compile_pass_manager.cpp:352] [UNILOG][INFO] Compile mode: dpu
I20241110 00:52:34.651924   588 compile_pass_manager.cpp:353] [UNILOG][INFO] Debug mode: null
I20241110 00:52:34.651930   588 


[VAIQ_NOTE]: Find subgraph for convlike_fix_20:
node name:DetectMultiBackend::DetectMultiBackend/DetectionModel[model]/Detect[model]/Detect[24]/Conv2d[m]/ModuleList[2]/ret, op type:nndct_conv2d, output shape: [1, 15, 15, 42]



[VAIQ_NOTE]: Find subgraph for convlike_fix_20:
node name:DetectMultiBackend::DetectMultiBackend/DetectionModel[model]/Detect[model]/Detect[24]/Conv2d[m]/ModuleList[1]/ret.277, op type:nndct_conv2d, output shape: [1, 30, 30, 42]



[VAIQ_NOTE]: Find subgraph for eltwise_fix_24:
node name:DetectMultiBackend::DetectMultiBackend/DetectionModel[model]/C3[model]/C3[8]/Sequential[m]/Bottleneck[0]/ret.137, op type:nndct_elemwise_add, output shape: [1, 15, 15, 128]



[VAIQ_NOTE]: Find subgraph for eltwise_fix_24:
node name:DetectMultiBackend::DetectMultiBackend/DetectionModel[model]/C3[model]/C3[2]/Sequential[m]/Bottleneck[0]/ret.23, op type:nndct_elemwise_add, output shape: [1, 120, 120, 16]



[VAIQ_NOTE]: Find subgraph for eltwise_fix_24:
node name:DetectMultiBacke

I20241110 00:52:34.849854   588 compile_pass_manager.cpp:465] [UNILOG][INFO] Graph name: nndct_conv2d_3WBlvJILY9eoyqSN, with op num: 8
I20241110 00:52:34.849857   588 compile_pass_manager.cpp:478] [UNILOG][INFO] Begin to compile...
I20241110 00:52:34.851996   588 compile_pass_manager.cpp:489] [UNILOG][INFO] Total device subgraph number 3, DPU subgraph number 1
I20241110 00:52:34.852010   588 compile_pass_manager.cpp:504] [UNILOG][INFO] Compile done.
I20241110 00:52:34.854808   588 compile_pass_manager.cpp:352] [UNILOG][INFO] Compile mode: dpu
I20241110 00:52:34.854836   588 compile_pass_manager.cpp:353] [UNILOG][INFO] Debug mode: null
I20241110 00:52:34.854842   588 compile_pass_manager.cpp:357] [UNILOG][INFO] Target architecture: DPUCZDX8G_ISA1_B4096
I20241110 00:52:34.854873   588 compile_pass_manager.cpp:465] [UNILOG][INFO] Graph name: nndct_conv2d_2Rozv7tHOiUApITS, with op num: 8
I20241110 00:52:34.854876   588 compile_pass_manager.cpp:478] [UNILOG][INFO] Begin to compile...
I20241


[VAIQ_NOTE]: Dot image is generated.(inspect/inspect_DPUCZDX8G_ISA1_B4096.png)

[VAIQ_NOTE]: =>Finish inspecting.


##### Inspection result anaysis:
1. Layers assigned to the CPU are shown in <font color=red>red circle</font> in the dot image. The reasons for being allocated to the CPU are shown in the column of hardware constraints.
2. The target device of an input node is determined by its consumer.
3. Due to data layout difference between Pytorch('NCHW') and XIR('NHWC'), if quantizer inserts some permutes(which the node message in inspect file will inform us about), these permutes may prevent the entire model from being deployed to the target device. Sometimes, we can cancel out this automatically inserted permute by inserting a permute in the original float model, sometimes, we can't.
4. If you want more details about the inspection, see the inspection report under the output directory you specified.
5. The dot image can help you to analyze inspection result in a more intuitive way. "svg" and "png" format are both supported.


In [9]:
# Show the dot image
from IPython.display import Image
Image('inspect/inspect_DPUCZDX8G_ISA1_B4096.png')

##### How to deploy this entire model on DPU:
1. Find the location of CPU operations in original model. All the details of operations are shown in inspect_{target}.txt, including source range, points to a source which is a stack track and helps to find the exact location of this operation in source code. Take resize op as a example, from source range, we can find the location of resize op in #3 input block line 11.  
node name: ToyModel::ToyModel/Upsample[upsample]/input.3  
...  
op type: resize  
...  
source range:  
...  
<font color=red>ipython-input-3-7ec1fc6b678f(11): forward</font>  
...

2. Modify the original model according to the hardware constrains message and try to cancel out the permute inserted by quantizer with by inserting a permute in the original float model(more details see hints in inspect_{target}.txt)

# Quantizer

#### What is quantizer ?  
   The inference process is computationally intensive and requires a high memory bandwidth to satisfy the low-latency and high-throughput requirements of Edge applications.
Quantization and channel pruning techniques address these challenges while simultaneously achieving optimal performance and high energy efficiency with minimal degradation in accuracy. Through quantization, integer computing units become viable, and weights and activations can be represented with reduced precision.

In [10]:
from pytorch_nndct.apis import torch_quantizer

In [11]:
from torchvision import datasets, transforms
from torch.utils.data import DataLoader

# Set up transformation and data loader
transform = transforms.Compose([
    transforms.Resize((480, 480)),  # Resize to the model input size
    transforms.ToTensor(),
])
calibration_dataset = datasets.ImageFolder("jupyter_notebooks/dms_yolov5n/image", transform=transform)
calibration_loader = DataLoader(calibration_dataset, batch_size=1, shuffle=False)

# Get a single batch of calibration data
calibration_data, _ = next(iter(calibration_loader))

In [12]:
# 예제 입력 데이터 생성 (여기서는 3채널 480x480 이미지 사용 예시)
dummy_input = torch.randn([1, 3, 480, 480], device=device)  # 배치 크기 1

quant_mode = 'calib'
quantizer = torch_quantizer(quant_mode, model, dummy_input, device=device, bitwidth=8, target=target)

quant_model = quantizer.quant_model


[VAIQ_NOTE]: OS and CPU information:
               system --- Linux
                 node --- 99adb10b6507
              release --- 5.15.153.1-microsoft-standard-WSL2
              version --- #1 SMP Fri Mar 29 23:14:13 UTC 2024
              machine --- x86_64
            processor --- x86_64

[VAIQ_NOTE]: Tools version information:
                  GCC --- GCC 7.5.0
               python --- 3.8.6
              pytorch --- 1.13.1+cu117
        vai_q_pytorch --- 3.5.0+60df3f1+torch1.13.1+cu117

[VAIQ_NOTE]: Quant config file is empty, use default quant configuration

[VAIQ_NOTE]: Quantization calibration process start up...

[VAIQ_NOTE]: =>Quant Module is in 'cuda'.

[VAIQ_NOTE]: =>Parsing DetectMultiBackend...

[VAIQ_NOTE]: Start to trace and freeze model...

[VAIQ_NOTE]: The input model nndct_st_DetectMultiBackend_ed is torch.nn.Module.

[VAIQ_NOTE]: Finish tracing.

[VAIQ_NOTE]: Processing ops...


██████████████████████████████████████████████████| 201/201 [00:00<00:00, 1145.79it/s, OpInfo: name = return_0, type = Return]           



[VAIQ_NOTE]: =>Doing weights equalization...

[VAIQ_NOTE]: =>Quantizable module is generated.(quantize_result/DetectMultiBackend.py)

[VAIQ_NOTE]: Find subgraph for convlike_fix_18:
node name:DetectMultiBackend::DetectMultiBackend/DetectionModel[model]/C3[model]/C3[2]/Conv[cv2]/Conv2d[conv]/ret.25, op type:nndct_conv2d, output shape: [1, 120, 120, 16]
node name:DetectMultiBackend::DetectMultiBackend/DetectionModel[model]/C3[model]/C3[2]/Conv[cv2]/LeakyReLU[act]/13446, op type:nndct_leaky_relu, output shape: [1, 120, 120, 16]



[VAIQ_NOTE]: Find subgraph for convlike_fix_18:
node name:DetectMultiBackend::DetectMultiBackend/DetectionModel[model]/C3[model]/C3[23]/Sequential[m]/Bottleneck[0]/Conv[cv1]/Conv2d[conv]/ret.257, op type:nndct_conv2d, output shape: [1, 15, 15, 128]
node name:DetectMultiBackend::DetectMultiBackend/DetectionModel[model]/C3[model]/C3[23]/Sequential[m]/Bottleneck[0]/Conv[cv1]/LeakyReLU[act]/14964, op type:nndct_leaky_relu, output shape: [1, 15, 15, 128]



[VAIQ_NO

I20241110 00:52:42.608059   588 compile_pass_manager.cpp:352] [UNILOG][INFO] Compile mode: dpu
I20241110 00:52:42.608093   588 compile_pass_manager.cpp:353] [UNILOG][INFO] Debug mode: null
I20241110 00:52:42.608098   588 compile_pass_manager.cpp:357] [UNILOG][INFO] Target architecture: DPUCZDX8G_ISA1_B4096
I20241110 00:52:42.608156   588 compile_pass_manager.cpp:465] [UNILOG][INFO] Graph name: nndct_conv2d_nndct_leaky_relu_DAYKnmtVXbxawvu7, with op num: 9
I20241110 00:52:42.608161   588 compile_pass_manager.cpp:478] [UNILOG][INFO] Begin to compile...
I20241110 00:52:42.610473   588 compile_pass_manager.cpp:489] [UNILOG][INFO] Total device subgraph number 3, DPU subgraph number 1
I20241110 00:52:42.610489   588 compile_pass_manager.cpp:504] [UNILOG][INFO] Compile done.
I20241110 00:52:42.613291   588 compile_pass_manager.cpp:352] [UNILOG][INFO] Compile mode: dpu
I20241110 00:52:42.613303   588 compile_pass_manager.cpp:353] [UNILOG][INFO] Debug mode: null
I20241110 00:52:42.613306   588 


[VAIQ_NOTE]: Find subgraph for convlike_fix_18:
node name:DetectMultiBackend::DetectMultiBackend/DetectionModel[model]/C3[model]/C3[6]/Sequential[m]/Bottleneck[2]/Conv[cv1]/Conv2d[conv]/ret.101, op type:nndct_conv2d, output shape: [1, 30, 30, 64]
node name:DetectMultiBackend::DetectMultiBackend/DetectionModel[model]/C3[model]/C3[6]/Sequential[m]/Bottleneck[2]/Conv[cv1]/LeakyReLU[act]/13930, op type:nndct_leaky_relu, output shape: [1, 30, 30, 64]



[VAIQ_NOTE]: Find subgraph for convlike_fix_18:
node name:DetectMultiBackend::DetectMultiBackend/DetectionModel[model]/C3[model]/C3[6]/Sequential[m]/Bottleneck[1]/Conv[cv2]/Conv2d[conv]/ret.95, op type:nndct_conv2d, output shape: [1, 30, 30, 64]
node name:DetectMultiBackend::DetectMultiBackend/DetectionModel[model]/C3[model]/C3[6]/Sequential[m]/Bottleneck[1]/Conv[cv2]/LeakyReLU[act]/13898, op type:nndct_leaky_relu, output shape: [1, 30, 30, 64]



[VAIQ_NOTE]: Find subgraph for convlike_fix_18:
node name:DetectMultiBackend::DetectMultiBacke

I20241110 00:52:42.808674   588 compile_pass_manager.cpp:465] [UNILOG][INFO] Graph name: nndct_conv2d_nndct_leaky_relu_z0kGqtVyZ2EhHgUI, with op num: 9
I20241110 00:52:42.808677   588 compile_pass_manager.cpp:478] [UNILOG][INFO] Begin to compile...
I20241110 00:52:42.811818   588 compile_pass_manager.cpp:489] [UNILOG][INFO] Total device subgraph number 3, DPU subgraph number 1
I20241110 00:52:42.811834   588 compile_pass_manager.cpp:504] [UNILOG][INFO] Compile done.
I20241110 00:52:42.815928   588 compile_pass_manager.cpp:352] [UNILOG][INFO] Compile mode: dpu
I20241110 00:52:42.815954   588 compile_pass_manager.cpp:353] [UNILOG][INFO] Debug mode: null
I20241110 00:52:42.815960   588 compile_pass_manager.cpp:357] [UNILOG][INFO] Target architecture: DPUCZDX8G_ISA1_B4096
I20241110 00:52:42.816004   588 compile_pass_manager.cpp:465] [UNILOG][INFO] Graph name: nndct_conv2d_nndct_leaky_relu_kb18ROPXExWIQKo0, with op num: 9
I20241110 00:52:42.816006   588 compile_pass_manager.cpp:478] [UNILOG


[VAIQ_NOTE]: Find subgraph for concat_fix_13:
node name:DetectMultiBackend::DetectMultiBackend/DetectionModel[model]/Concat[model]/Concat[16]/ret.195, op type:nndct_concat, output shape: [1, 60, 60, 128]



[VAIQ_NOTE]: Find subgraph for concat_fix_13:
node name:DetectMultiBackend::DetectMultiBackend/DetectionModel[model]/C3[model]/C3[23]/ret.269, op type:nndct_concat, output shape: [1, 15, 15, 256]



[VAIQ_NOTE]: Find subgraph for concat_fix_13:
node name:DetectMultiBackend::DetectMultiBackend/DetectionModel[model]/C3[model]/C3[20]/ret.241, op type:nndct_concat, output shape: [1, 30, 30, 128]



[VAIQ_NOTE]: Find subgraph for convlike_fix_20:
node name:DetectMultiBackend::DetectMultiBackend/DetectionModel[model]/Detect[model]/Detect[24]/Conv2d[m]/ModuleList[0]/ret.275, op type:nndct_conv2d, output shape: [1, 60, 60, 42]



[VAIQ_NOTE]: Find subgraph for convlike_fix_20:
node name:DetectMultiBackend::DetectMultiBackend/DetectionModel[model]/Detect[model]/Detect[24]/Conv2d[m]/ModuleLi

I20241110 00:52:43.013698   588 compile_pass_manager.cpp:352] [UNILOG][INFO] Compile mode: dpu
I20241110 00:52:43.013720   588 compile_pass_manager.cpp:353] [UNILOG][INFO] Debug mode: null
I20241110 00:52:43.013724   588 compile_pass_manager.cpp:357] [UNILOG][INFO] Target architecture: DPUCZDX8G_ISA1_B4096
I20241110 00:52:43.013751   588 compile_pass_manager.cpp:465] [UNILOG][INFO] Graph name: nndct_concat_jNGxbH0tK4yIWFB1, with op num: 6
I20241110 00:52:43.013753   588 compile_pass_manager.cpp:478] [UNILOG][INFO] Begin to compile...
I20241110 00:52:43.015174   588 compile_pass_manager.cpp:489] [UNILOG][INFO] Total device subgraph number 4, DPU subgraph number 1
I20241110 00:52:43.015189   588 compile_pass_manager.cpp:504] [UNILOG][INFO] Compile done.
I20241110 00:52:43.017814   588 compile_pass_manager.cpp:352] [UNILOG][INFO] Compile mode: dpu
I20241110 00:52:43.017838   588 compile_pass_manager.cpp:353] [UNILOG][INFO] Debug mode: null
I20241110 00:52:43.017843   588 compile_pass_mana

In [13]:
# Forward pass 수행
quantizer.quant_model(dummy_input)  # forward pass 수행

# 이제 quantizer.export_quant_config()를 호출하여 양자화 결과를 내보낼 수 있습니다.
quantizer.export_quant_config()


[VAIQ_NOTE]: =>Get module with quantization.


/opt/vitis_ai/conda/envs/vitis-ai-pytorch/lib/python3.8/site-packages/pytorch_nndct/quantization/torchquantizer.py:223: FutureWarning: Unlike other reduction functions (e.g. `skew`, `kurtosis`), the default behavior of `mode` typically preserves the axis it acts along. In SciPy 1.11.0, this behavior will change: the default value of `keepdims` will become False, the `axis` over which the statistic is taken will be eliminated, and the value None will no longer be accepted. Set `keepdims` to True or False to avoid this warning.
  bnfp[1] = stats.mode(data)[0][0]



[VAIQ_NOTE]: =>Exporting quant config.(quantize_result/quant_info.json)


In [14]:
quant_mode = 'test'
quantizer = torch_quantizer(quant_mode, model, dummy_input, device=device, bitwidth=8, target=target)
quant_model = quantizer.quant_model


[VAIQ_NOTE]: OS and CPU information:
               system --- Linux
                 node --- 99adb10b6507
              release --- 5.15.153.1-microsoft-standard-WSL2
              version --- #1 SMP Fri Mar 29 23:14:13 UTC 2024
              machine --- x86_64
            processor --- x86_64

[VAIQ_NOTE]: Tools version information:
                  GCC --- GCC 7.5.0
               python --- 3.8.6
              pytorch --- 1.13.1+cu117
        vai_q_pytorch --- 3.5.0+60df3f1+torch1.13.1+cu117

[VAIQ_NOTE]: Quant config file is empty, use default quant configuration

[VAIQ_NOTE]: Quantization test process start up...

[VAIQ_NOTE]: =>Quant Module is in 'cuda'.

[VAIQ_NOTE]: =>Parsing DetectMultiBackend...

[VAIQ_NOTE]: Start to trace and freeze model...

[VAIQ_NOTE]: The input model nndct_st_DetectMultiBackend_ed is torch.nn.Module.

[VAIQ_NOTE]: Finish tracing.

[VAIQ_NOTE]: Processing ops...


██████████████████████████████████████████████████| 201/201 [00:00<00:00, 1161.89it/s, OpInfo: name = return_0, type = Return]           



[VAIQ_NOTE]: =>Doing weights equalization...

[VAIQ_NOTE]: =>Quantizable module is generated.(quantize_result/DetectMultiBackend.py)

[VAIQ_NOTE]: Find subgraph for convlike_fix_18:
node name:DetectMultiBackend::DetectMultiBackend/DetectionModel[model]/C3[model]/C3[2]/Conv[cv2]/Conv2d[conv]/ret.25, op type:nndct_conv2d, output shape: [1, 120, 120, 16]
node name:DetectMultiBackend::DetectMultiBackend/DetectionModel[model]/C3[model]/C3[2]/Conv[cv2]/LeakyReLU[act]/13446, op type:nndct_leaky_relu, output shape: [1, 120, 120, 16]



[VAIQ_NOTE]: Find subgraph for convlike_fix_18:
node name:DetectMultiBackend::DetectMultiBackend/DetectionModel[model]/C3[model]/C3[23]/Sequential[m]/Bottleneck[0]/Conv[cv1]/Conv2d[conv]/ret.257, op type:nndct_conv2d, output shape: [1, 15, 15, 128]
node name:DetectMultiBackend::DetectMultiBackend/DetectionModel[model]/C3[model]/C3[23]/Sequential[m]/Bottleneck[0]/Conv[cv1]/LeakyReLU[act]/14964, op type:nndct_leaky_relu, output shape: [1, 15, 15, 128]



[VAIQ_NO

I20241110 00:52:45.257445   588 compile_pass_manager.cpp:352] [UNILOG][INFO] Compile mode: dpu
I20241110 00:52:45.257483   588 compile_pass_manager.cpp:353] [UNILOG][INFO] Debug mode: null
I20241110 00:52:45.257489   588 compile_pass_manager.cpp:357] [UNILOG][INFO] Target architecture: DPUCZDX8G_ISA1_B4096
I20241110 00:52:45.257532   588 compile_pass_manager.cpp:465] [UNILOG][INFO] Graph name: nndct_conv2d_nndct_leaky_relu_bk9zy8FlTCEQSspc, with op num: 9
I20241110 00:52:45.257535   588 compile_pass_manager.cpp:478] [UNILOG][INFO] Begin to compile...
I20241110 00:52:45.259825   588 compile_pass_manager.cpp:489] [UNILOG][INFO] Total device subgraph number 3, DPU subgraph number 1
I20241110 00:52:45.259841   588 compile_pass_manager.cpp:504] [UNILOG][INFO] Compile done.
I20241110 00:52:45.262677   588 compile_pass_manager.cpp:352] [UNILOG][INFO] Compile mode: dpu
I20241110 00:52:45.262704   588 compile_pass_manager.cpp:353] [UNILOG][INFO] Debug mode: null
I20241110 00:52:45.262712   588 


[VAIQ_NOTE]: Find subgraph for convlike_fix_18:
node name:DetectMultiBackend::DetectMultiBackend/DetectionModel[model]/C3[model]/C3[8]/Sequential[m]/Bottleneck[0]/Conv[cv2]/Conv2d[conv]/ret.133, op type:nndct_conv2d, output shape: [1, 15, 15, 128]
node name:DetectMultiBackend::DetectMultiBackend/DetectionModel[model]/C3[model]/C3[8]/Sequential[m]/Bottleneck[0]/Conv[cv2]/LeakyReLU[act]/14140, op type:nndct_leaky_relu, output shape: [1, 15, 15, 128]



[VAIQ_NOTE]: Find subgraph for convlike_fix_18:
node name:DetectMultiBackend::DetectMultiBackend/DetectionModel[model]/C3[model]/C3[6]/Sequential[m]/Bottleneck[2]/Conv[cv1]/Conv2d[conv]/ret.101, op type:nndct_conv2d, output shape: [1, 30, 30, 64]
node name:DetectMultiBackend::DetectMultiBackend/DetectionModel[model]/C3[model]/C3[6]/Sequential[m]/Bottleneck[2]/Conv[cv1]/LeakyReLU[act]/13930, op type:nndct_leaky_relu, output shape: [1, 30, 30, 64]



[VAIQ_NOTE]: Find subgraph for convlike_fix_18:
node name:DetectMultiBackend::DetectMultiBa

I20241110 00:52:45.457820   588 compile_pass_manager.cpp:352] [UNILOG][INFO] Compile mode: dpu
I20241110 00:52:45.457844   588 compile_pass_manager.cpp:353] [UNILOG][INFO] Debug mode: null
I20241110 00:52:45.457850   588 compile_pass_manager.cpp:357] [UNILOG][INFO] Target architecture: DPUCZDX8G_ISA1_B4096
I20241110 00:52:45.457890   588 compile_pass_manager.cpp:465] [UNILOG][INFO] Graph name: nndct_conv2d_nndct_leaky_relu_nTvasWqIEYLxR9ig, with op num: 9
I20241110 00:52:45.457893   588 compile_pass_manager.cpp:478] [UNILOG][INFO] Begin to compile...
I20241110 00:52:45.460563   588 compile_pass_manager.cpp:489] [UNILOG][INFO] Total device subgraph number 3, DPU subgraph number 1
I20241110 00:52:45.460578   588 compile_pass_manager.cpp:504] [UNILOG][INFO] Compile done.
I20241110 00:52:45.463905   588 compile_pass_manager.cpp:352] [UNILOG][INFO] Compile mode: dpu
I20241110 00:52:45.463928   588 compile_pass_manager.cpp:353] [UNILOG][INFO] Debug mode: null
I20241110 00:52:45.463933   588 


[VAIQ_NOTE]: Find subgraph for concat_fix_13:
node name:DetectMultiBackend::DetectMultiBackend/DetectionModel[model]/C3[model]/C3[8]/ret.143, op type:nndct_concat, output shape: [1, 15, 15, 256]



[VAIQ_NOTE]: Find subgraph for concat_fix_13:
node name:DetectMultiBackend::DetectMultiBackend/DetectionModel[model]/Concat[model]/Concat[16]/ret.195, op type:nndct_concat, output shape: [1, 60, 60, 128]



[VAIQ_NOTE]: Find subgraph for concat_fix_13:
node name:DetectMultiBackend::DetectMultiBackend/DetectionModel[model]/C3[model]/C3[23]/ret.269, op type:nndct_concat, output shape: [1, 15, 15, 256]



[VAIQ_NOTE]: Find subgraph for concat_fix_13:
node name:DetectMultiBackend::DetectMultiBackend/DetectionModel[model]/C3[model]/C3[20]/ret.241, op type:nndct_concat, output shape: [1, 30, 30, 128]



[VAIQ_NOTE]: Find subgraph for convlike_fix_20:
node name:DetectMultiBackend::DetectMultiBackend/DetectionModel[model]/Detect[model]/Detect[24]/Conv2d[m]/ModuleList[0]/ret.275, op type:nndct_conv2

I20241110 00:52:45.662635   588 compile_pass_manager.cpp:352] [UNILOG][INFO] Compile mode: dpu
I20241110 00:52:45.662662   588 compile_pass_manager.cpp:353] [UNILOG][INFO] Debug mode: null
I20241110 00:52:45.662667   588 compile_pass_manager.cpp:357] [UNILOG][INFO] Target architecture: DPUCZDX8G_ISA1_B4096
I20241110 00:52:45.662699   588 compile_pass_manager.cpp:465] [UNILOG][INFO] Graph name: nndct_concat_lsLCDM8ZNB30T5XV, with op num: 6
I20241110 00:52:45.662703   588 compile_pass_manager.cpp:478] [UNILOG][INFO] Begin to compile...
I20241110 00:52:45.664470   588 compile_pass_manager.cpp:489] [UNILOG][INFO] Total device subgraph number 4, DPU subgraph number 1
I20241110 00:52:45.664489   588 compile_pass_manager.cpp:504] [UNILOG][INFO] Compile done.
I20241110 00:52:45.668824   588 compile_pass_manager.cpp:352] [UNILOG][INFO] Compile mode: dpu
I20241110 00:52:45.668861   588 compile_pass_manager.cpp:353] [UNILOG][INFO] Debug mode: null
I20241110 00:52:45.668869   588 compile_pass_mana

In [15]:
# Forward pass 수행
quantizer.quant_model(dummy_input)  # forward pass 수행

quantizer.export_xmodel(deploy_check=False)


[VAIQ_NOTE]: =>Get module with quantization.

[VAIQ_NOTE]: =>Converting to xmodel ...

[VAIQ_NOTE]: =>Successfully convert 'DetectMultiBackend' to xmodel.(quantize_result/DetectMultiBackend_int.xmodel)


### Quantize done
next process is complie .xmodel
```
vai_c_xir -x /PATH/TO/quantized.xmodel -a /PATH/TO/arch.json -o /OUTPUTPATH -n netname
```
example
```
vai_c_xir -x ./DetectMultiBackend_int.xmodel -a /opt/vitis_ai/compiler/arch/DPUCZDX8G/KV260/arch.json -o ./compile/ -n model
```